# into my eyes

In [ ]:
from collections import Counter
from io import StringIO
from matplotlib import pyplot as plt
from pathlib import Path
from tqdm import tqdm
import json
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import pickle
import re
import seaborn as sns
import openpyxl
from collections import defaultdict
from captum.attr import visualization
from tqdm import tqdm

## datasets

Loading and mergin dataset

In [ ]:
data_text = ""

for filename in sorted(["ds", "ts_hs", "ts_ht"]):
    with open(
        Path("datasets", "task_0", f"{filename}.tsv"), "rt", encoding="utf8"
    ) as f:
        data_text += f.read()

df = pd.read_csv(StringIO(data_text), sep="\t")
df = df.drop_duplicates().reset_index(names="old_idx").reset_index(names="new_idx")

splitting the dataset in training and testing (following previous works)

In [ ]:
# lookup = df.set_index("old_idx")["new_idx"]
# pth = Path("datasets", "task_0", "train_test_splitting.json")
# idx = json.load(open(pth, "rt"))
# idx = {k: [lookup[i] for i in lst if i in lookup] for k, lst in idx.items()}

In [ ]:
# x, y = df["raw_text"], df["label"]
# x_train, x_test = x.loc[idx["train"]], x.loc[idx["test"]]
# y_train, y_test = y.loc[idx["train"]].astype(int), y.loc[idx["test"]].astype(int)

loading psycologist highlights

In [ ]:
wb = openpyxl.load_workbook('datasets/task_0/Testset.xlsx')
sheet = wb.active

In [ ]:
yellow, no_highlight = list(), list()

In [ ]:
for row in range(2, 1105):
    uid = sheet[f"A{row}"].value
    text = sheet[f"B{row}"].value
    pattern = sheet[f"C{row}"].value
    if pattern is not None and pattern.strip():
        yellow.append((uid, text, pattern))
    else:
        no_highlight.append((uid, text))

In [ ]:
df_yellow = pd.DataFrame(yellow, columns=["idx", "text", "pattern"])
df_val = pd.merge(df, df_yellow, left_on="raw_text", right_on="text")
df = df.loc[~df.new_idx.isin(df_val.new_idx)]

In [ ]:
X, y = df["pp_text"], df.label.astype(int)

## models

### born

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split
from bornrule import BornClassifier

In [ ]:
vect = TfidfVectorizer()
tfidf_mx = vect.fit_transform(X).toarray()
words = vect.get_feature_names_out()

In [ ]:
W = words.shape[0]

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(
    tfidf_mx,
    y,
    test_size=0.2,
    random_state=42,
    stratify=y,
)

In [ ]:
amplitude = 0.5 #amplitude
balance = 1 #balance
entropy = 1 #entropy

In [ ]:
born = BornClassifier(a=amplitude, b=balance, h=entropy)
born.fit(X=X_train, y=y_train)

In [ ]:
from erisk import metrics

In [ ]:
y_hat = born.predict(X_test)
metrics(y_hat, y_test)

In [ ]:
born.classes_

In [ ]:
weights = born.explain()[:,1]
scores = sorted(list(zip(words, weights)), key = lambda x : x[-1], reverse=True)
kwscores = defaultdict(float, scores)

let's see locally

In [ ]:
yellow_born = vect.transform(df_val.pp_text).toarray()


In [ ]:
vis_data_records = list()
for idx, v in tqdm(enumerate(yellow_born)):
    sample = v.reshape((1, W))
    weights = born.explain(sample)[:, 1]
    scores = sorted(list(zip(words, weights)), key=lambda x: x[-1], reverse=True)
    kwscores = defaultdict(float, scores)

    tokens = df_val.loc[idx, "pp_text"].split()
    a = np.array([kwscores[w] for w in tokens])
    a = (a - a.mean())/(a.std())
    vis_data_records.append(
        visualization.VisualizationDataRecord(
            pred_prob=0.68,  # (Predicted Label)
            pred_class="depress",  # Predicted Label
            word_attributions=a,
            true_class="depress",  # True Label, ground-truth label of the input
            attr_class=idx,  # Attribution Label, the input
            attr_score=sum(a),  # Attribution Score, the sum of IG accross the whole tokens
            raw_input_ids=tokens,  # the list of tokens
            convergence_score=0,  # the difference between approximated and true integrated gradients
        )
    )
visualization.visualize_text(vis_data_records)


### roberta

In [342]:
import torch
torch.cuda.get_device_name(0)

'NVIDIA GeForce GTX 1050'

In [338]:
from transformers import (
    Trainer,
    TrainingArguments,
    AutoTokenizer,
    DataCollatorWithPadding,
    AutoModelForSequenceClassification,
)
from datasets import load_dataset
import datasets

In [339]:
tokenizer_hf = AutoTokenizer.from_pretrained("ShreyaR/finetuned-roberta-depression")
model = AutoModelForSequenceClassification.from_pretrained("ranieri-unimi/test-trainer")

In [337]:
text = df_val.loc[1, "raw_text"]
text

'It comes back to that thing where I feel like I hurt people more than I could give them. :/'

In [350]:
vis_data_records = list()
for idx, text in tqdm(df_val.raw_text.items()):

    input_ids = tokenizer_hf.encode(text, return_tensors="pt", padding=True, truncation=True)
    outputs = model(
        input_ids,
        output_attentions=True,
        # attention_mask=attention_mask,
    )
    attention_weights = outputs[-1]
    attention_norms = attention_weights[-1][0, :, :, :].norm(dim=0)
    a = attention_norms[0, 1:-1].cpu().detach().numpy()
    tokens = [tokenizer_hf.decode(e).lower().strip() for e in input_ids[0, 1:-1]]

    # a = np.exp(a)/sum(np.exp(a))
    a = (a - a.mean())/(a.std())
    vis_data_records.append(
        visualization.VisualizationDataRecord(
            pred_prob=0.68,  # (Predicted Label)
            pred_class="depress",  # Predicted Label
            word_attributions=a,
            true_class="depress",  # True Label, ground-truth label of the input
            attr_class=idx,  # Attribution Label, the input
            attr_score=sum(a),  # Attribution Score, the sum of IG accross the whole tokens
            raw_input_ids=tokens,  # the list of tokens
            convergence_score=0,  # the difference between approximated and true integrated gradients
        )
    )
visualization.visualize_text(vis_data_records)


161it [00:54,  2.94it/s]


### lex